In [72]:
# %load http://che.byu.edu/imports.py
import numpy             as np
import matplotlib.pyplot as plt
%matplotlib inline
from scipy.optimize      import fsolve, curve_fit
from scipy.integrate     import odeint, quad
from scipy.interpolate   import interp1d
from scipy.misc          import derivative
import scipy.constants   as const
import sympy             as sp
sp.init_printing()
import glob
import time
#import pint; u = pint.UnitRegistry()

Problem 13.8 for ChEn 733

In [157]:
Tg = 1800   #K
Ptot = 1    #atm
PO2g = .1   #atm
dpm = 500    #particle diameter in microns
dp = dpm*1e-4 #particle diameter in cm
Tp = 1800   #K
Nu = 2       #Nusselt number
Sh = 2       #Sherwood number
#eps = 0.8    #particle emissivity
#sigma = 1.3552E-15   #StefanBoltzman constant in kcal/cm^2/K^4
#Twall = 1250 #Wall temperature in K
#print("Twall = ",Twall)
Carbonfrac = 0.80
n = 0.5
Rcal = 1.987
Rgas = 82.05    #cm^3-atm/gmol/K
Ea = -5.9+0.355*Carbonfrac*100   #Activation Energy in kcal/gmol
#Ea = 30      # kcal/mol
lnk_1750 = (2.8-0.076*Carbonfrac*100)
A = np.exp(lnk_1750 + Ea*1000/(Rcal*1750))   #g-C/cm^2/s/atm^0.5
#A = 31.59e-5*.1384
print('Ea (kcal/mol) = ',Ea)
print('A g-C/cm^2/s/atm^0.5', A)
#COtoCO2 = 11.3
DelH_CO = 26.4   #kcal/mol C
DelH_CO2 = 94.1  #kcal/mol C
net_DelH = DelH_CO
#net_DelH = COtoCO2/(1+COtoCO2)*DelH_CO+1/(1+COtoCO2)*DelH_CO2
#print("net_DelH = ",net_DelH)
#stoich = COtoCO2/(1+COtoCO2)*2+1/(1+COtoCO2)*1   #moles C per mole O2
stoich = 2

Ea (kcal/mol) =  22.5
A g-C/cm^2/s/atm^0.5 24.30374678143053


Calculate the diffusivity

In [158]:
def diff(Tfilm,Ptot):
#   Uses correlation from Mitchell report. 
#   diffusivity is in cm^2/s
    diff = 0.00001523*Tfilm**1.67/Ptot
    return diff

Calculate the thermal conductivity

In [159]:
def kg(Tfilm):
    kg =(0.00000076893*Tfilm**0.7722)/1000   #kcal/cm/s/K
    return kg

Calculate the actual diffusion rate

In [160]:
def ActDiffrate(Tg,Tp,PO2s):
    Tfilm = (Tg + Tp)/2
# Reaction Rate calculation
    km = Sh*diff(Tfilm,Ptot)/dp     #Mass transfer coefficient
#    print('PO2g',PO2g,'PO2s',PO2s,'Tg',Tg)
    Diffrate = km*(PO2g/(0.08205*Tg*1000)-PO2s/(0.08205*Tg*1000))*stoich*12
    return Diffrate

Calculate the surface reaction rate

In [161]:
def ActRxnrate(Tp,PO2s):
    Rxnrate = A*np.exp(-Ea*1000/(Rcal*Tp))*(PO2s)**n
    return Rxnrate

This function sets the diffusion rate equal to the surface reaction rate by adjusting $P_{O2,s}$, and also calculates the particle temperature by setting the energy balance to zero

In [162]:
def Balances(PO2s0):
# Set diffusion rate = surface reaction rate
#    Tp = Variables[0]
    PO2s = PO2s0
    Drate = ActDiffrate(Tg,Tp,PO2s)
    Srate = ActRxnrate(Tp,PO2s)
    Tfilm = (Tg + Tp)/2
    Deltarate =Drate-Srate
    print(PO2s,Tg,Tp,Deltarate)
# Energy balance calculation
#    h = Nu*kg(Tfilm)/dp
#    qconv = h*(Tg-Tp)
#    qrad = eps*sigma*(Twall**4 - Tp**4)
#    qrxn = Drate*net_DelH/12   #reaction rate times the heat of reaction
#    Netq = qconv + qrad + qrxn
#    Balances = abs(Deltarate) + abs(Netq)
    Balances = abs(Deltarate)
    return Deltarate

Now solve the rate and energy function simultaneously

In [163]:
PO2s0 = .001
print("PO2s0 = ",PO2s0, "Tp = ",Tp)
#Variables = np.array([Tp0,PO2s])
#print(Variables)
#Tnew = fsolve(Netq,Tp)
#print(Tp,Tnew)
solution = fsolve(Balances,PO2s0)
#Tp = solution[0]
PO2s = max(solution[0],1e-6)
#print('Tp =',Tp)
print('PO2s =',PO2s)

PO2s0 =  0.001 Tp =  1800
[0.001] 1800 1800 [0.00125225]
[0.001] 1800 1800 [0.00125225]
[0.001] 1800 1800 [0.00125225]
[0.001] 1800 1800 [0.00125225]
[0.00269419] 1800 1800 [0.00029296]
[0.00321158] 1800 1800 [6.4356626e-05]
[0.00335724] 1800 1800 [3.18194833e-06]
[0.00336482] 1800 1800 [3.43088877e-08]
[0.0033649] 1800 1800 [1.82627398e-11]
[0.0033649] 1800 1800 [1.04517089e-16]
[0.0033649] 1800 1800 [0.]
PO2s = 0.0033648981671889054


In [164]:
def MaxDiffrate(Tp):
    Tfilm1 = (Tg + Tp)/2
    km = Sh*diff(Tfilm1,Ptot)/dp     #Mass transfer coefficient
    MaxDiffrate = km*(PO2g/(0.08205*Tg*1000))*stoich*12
    return MaxDiffrate

Now calculate the ratio of the actual rate to the maximum possible diffusion rate

In [165]:
    Actrate = ActRxnrate(Tp,PO2s)
    Maxrate = MaxDiffrate(Tp)
    Chi = Actrate/Maxrate
    print('Tp =',Tp)
    print('PO2s =',PO2s)   
    print('actual reaction rate (g Carbon/cm^2/s) =',Actrate)
    print('maxim rate (g Carbon/cm^2/s) = ',Maxrate)
    print('chi factor =',Chi)

Tp = 1800
PO2s = 0.0033648981671889054
actual reaction rate (g Carbon/cm^2/s) = 0.002612522491645025
maxim rate (g Carbon/cm^2/s) =  0.0027034922529134025
chi factor = 0.9663510183281108
